# Tutorial 3 - Enzyme kinetics

In [ ]:
# preliminaries
%matplotlib widget
import numpy as np
from matplotlib import pyplot as plt
import scipy as sp
import scipy.optimize
import scipy.misc
import scipy.stats
import pandas as pd
import os
from lmfit import Model
backupdir = os.getcwd()

## Question 1

In [ ]:
def v(s,p,Ks,Kp,Vm,Keq):
    return Vm*s/Ks*(1-p/s/Keq)/(1+s/Ks+p/Kp)

In [ ]:
Ks = 1.0
Kp = 10.0
Vm = 2.0
Keq = 100.0
p = 0.0

### Question 1(a)

In [ ]:
s = np.linspace(0.01,10,101)
fig, ax = plt.subplots()
ax.plot(s, v(s,p,Ks,Kp,Vm,Keq))
ax.set_xlabel('[s]')
ax.set_ylabel('rate')

### Question 1(b)

In [ ]:
fig, ax = plt.subplots()
ax.plot(s, v(s,0,Ks,Kp,Vm,Keq), label='p=0')
ax.plot(s, v(s,1,Ks,Kp,Vm,Keq), label='p=1')
ax.plot(s, v(s,10,Ks,Kp,Vm,Keq), label='p=10')
ax.plot(s, v(s,100,Ks,Kp,Vm,Keq), label='p=100')
ax.plot(s, v(s,1000,Ks,Kp,Vm,Keq), label='p=1000')
ax.legend(loc='best')


In [ ]:
fig, ax = plt.subplots()
ax.plot(s, v(s,p,0.1,Kp,Vm,Keq), label='Ks=0.1')
ax.plot(s, v(s,p,0.5,Kp,Vm,Keq), label='Ks=0.5')
ax.plot(s, v(s,p,1,Kp,Vm,Keq), label='Ks=1')
ax.plot(s, v(s,p,5,Kp,Vm,Keq), label='Ks=5')
ax.plot(s, v(s,p,10,Kp,Vm,Keq), label='Ks=10')
ax.legend(loc='best')

In [ ]:
fig, ax = plt.subplots()
ax.plot(s, v(s,p,Ks,Kp,0,Keq), label='Vm=0')
ax.plot(s, v(s,p,Ks,Kp,2,Keq), label='Vm=2')
ax.plot(s, v(s,p,Ks,Kp,4,Keq), label='Vm=4')
ax.plot(s, v(s,p,Ks,Kp,6,Keq), label='Vm=6')
ax.plot(s, v(s,p,Ks,Kp,8,Keq), label='Vm=8')
ax.plot(s, v(s,p,Ks,Kp,10,Keq), label='Vm=10')
ax.legend(loc='best')

### Question 1(c)

In [ ]:
s=np.linspace(0.001,50,101)
fig, ax = plt.subplots()
ax.plot(s, s/v(s,p,Ks,Kp,Vm,Keq)*sp.misc.derivative(v, s, dx=0.0001, args=(p,Ks,Kp,Vm,Keq)))

In [ ]:
results = []
for s in np.linspace(0.001,50,101):
    vwild = v(s,p,Ks,Kp,Vm,Keq)
    vu = v(1.01*s,p,Ks,Kp,Vm,Keq)
    vd = v(0.99*s,p,Ks,Kp,Vm,Keq)
    elas = (vu - vd)/(2*0.01*vwild)
    results.append([s, elas])
results = np.array(results)

In [ ]:
results.shape

In [ ]:
fig, ax = plt.subplots()
ax.plot(results[:,0], results[:,1])

## Question 2

In [ ]:
def vHill(s,p,h):
    return 2.0*s*(1-p/s/1.0e6)*(s+p)**(h-1)/(1+(s+p)**h)

In [ ]:
p = 0.0

### Question 2(a)

In [ ]:
s = np.linspace(0.001, 5, 101)
fig, ax = plt.subplots()
ax.plot(s, vHill(s,p,1), label='h=1')
ax.plot(s, vHill(s,p,2), label='h=2')
ax.plot(s, vHill(s,p,3), label='h=3')
ax.plot(s, vHill(s,p,4), label='h=4')
ax.set_xlabel('[s]')
ax.set_ylabel('rate')
ax.legend(loc='best')
# ax.semilogy()

### Question 2(b)

In [ ]:
def elasHill(s,p,h):
    return s/vHill(s,p,h)*sp.misc.derivative(vHill, s, dx=0.00001, args=(p,h))

In [ ]:
fig, ax = plt.subplots()
ax.plot(s, elasHill(s,0,1), label='h=1')
ax.plot(s, elasHill(s,0,2), label='h=2')
ax.plot(s, elasHill(s,0,4), label='h=4')
ax.set_xlabel('[s]')
ax.set_ylabel('elasticity')
ax.legend(loc='best')

### Question 2(c)

In [ ]:
def vHillmod(x,alpha):
    return 2.0*1*(1-1/1/1.0e4)*(1+1/1e4)**(4-1)/((1+x**4)/(1+alpha*x**4)+(1+1/1e4)**4)

In [ ]:
x = np.linspace(0.001, 5, 501)
# x = np.logspace(-3,3,101)
fig, ax = plt.subplots()
ax.plot(x, vHillmod(x,1.0e-4), label=r'$\alpha=10^{-4}$')
ax.plot(x, vHillmod(x,1.0e4), label=r'$\alpha=10^4$')
ax.plot(x, vHillmod(x,1), label=r'$\alpha=1$')
ax.set_xlabel('[x]')
ax.set_ylabel('rate')
ax.legend(loc='best')
# ax.ylim(0,2.5)
# ax.loglog()

### Question 3

In [ ]:
s0 = pd.read_csv('s0mM.csv', sep=' ', names=['Time', 'NADH'])
s4 = pd.read_csv('s4mM.csv', sep=' ', names=['Time', 'NADH'])
s8 = pd.read_csv('s8mM.csv', sep=' ', names=['Time', 'NADH'])
s12 = pd.read_csv('s12mM.csv', sep=' ', names=['Time', 'NADH'])
s16 = pd.read_csv('s16mM.csv', sep=' ', names=['Time', 'NADH'])
s20 = pd.read_csv('s20mM.csv', sep=' ', names=['Time', 'NADH'])
s24 = pd.read_csv('s24mM.csv', sep=' ', names=['Time', 'NADH'])

### Question 3(a)

In [ ]:
# plot for 8mM
s8.plot(x='Time', y='NADH', kind='scatter')

In [ ]:
# plot for 20mM
s20.plot(x='Time', y='NADH', kind='scatter')

### Question 3(b)

In [ ]:
reg0 = sp.stats.linregress(s0)
reg4 = sp.stats.linregress(s4)
reg8 = sp.stats.linregress(s8)
reg12 = sp.stats.linregress(s12)
reg16 = sp.stats.linregress(s16)
reg20 = sp.stats.linregress(s20)
reg24 = sp.stats.linregress(s24)

In [ ]:
reg4

In [ ]:
regressions = [reg0, reg4, reg8, reg12, reg16, reg20, reg24]
rates = []
for reg in regressions:
    print(reg.slope)
    rates.append(reg.slope)
rates = np.array(rates)

In [ ]:
rates

### Question 3(c)

In [ ]:
concs = np.array([0.0, 4, 8, 12, 16, 20 , 24])
s_and_v = pd.DataFrame({'NADH': concs, 'rate': rates})

In [ ]:
s_and_v

In [ ]:
s_and_v.plot(x='NADH', y='rate', kind='scatter')

### Questions 3(d&e)

In [ ]:
# irreversible Michaelis-Menten (initial p=0)
def MM(s, Vm, Ks):
    return Vm*s/(Ks + s)

In [ ]:
mymod = Model(MM)
mypar = mymod.make_params(Vm=1,Ks=1)
myfit = mymod.fit(rates, mypar, s=concs)
myfit

In [ ]:
svals = np.linspace(0,25,101)
fig, ax = plt.subplots()
ax.plot(s_and_v.NADH, s_and_v.rate, 'o', label='data')
ax.plot(svals, myfit.eval(s=svals), label='fit')
ax.set_xlabel('[NADH] (mM)')
ax.set_ylabel('rate (mM/s)')
ax.legend(loc='best')